In [7]:
from trading_helper import TradingHelper
import sqlite3
import threading
import sqlite3
from ppi_client.models.order_budget import OrderBudget
from ppi_client.models.order_confirm import OrderConfirm
import json
import plotly.express as px
import plotly.graph_objs as go
import numpy as np
import string
from ppi_client.api.constants import ACCOUNTDATA_TYPE_ACCOUNT_NOTIFICATION, ACCOUNTDATA_TYPE_PUSH_NOTIFICATION, \
    ACCOUNTDATA_TYPE_ORDER_NOTIFICATION
from ppi_client.models.account_movements import AccountMovements
from ppi_client.models.order import Order
from ppi_client.ppi import PPI
from dotenv import load_dotenv
from datetime import datetime, timedelta
import os
import psycopg2
from datetime import datetime as dt
import pandas as pd
import time

# Obtener la fecha de hoy
today_start = datetime.now().strftime('%Y-%m-%d 00:00:00')
today_end = datetime.now().strftime('%Y/%m/%d 23:59:59.999999')

In [8]:
def latest_count():
    last_count=None
    conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password=os.getenv('CLAVE_POSGRES'),
        host="127.0.0.1"  # "/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )

    # Obtener la fecha de hoy
    today_start = dt.now().strftime('%Y/%m/%d 00:00:00.00')
    today_end = dt.now().strftime('%Y/%m/%d 23:59:59.999999')
    cursor = conn.cursor()
    cursor.execute(f"""
                    SELECT count
                    FROM precios
                    WHERE timestamp >= '{today_start}' 
                    AND timestamp <= '{today_end}'
                    AND short_ticker in ('T4X4','T5X4','T2X5','TDG24','TC25P','TX25','TX26','TX28','TZX25','TZX26',
            'TZX27','TZX28','TZXD5','TZXD6','TZXD7','TZV25','TV25','S30G4','S13S4','S30S4','S14O4',
            'S29N4','S17E5','S13D4','S31E5','S28F5','S31M5')
                    order by count desc
                    limit 1
                    """)
    columns = [desc[0] for desc in cursor.description]
    try: last_count = [dict(zip(columns, row)) for row in cursor.fetchall()][0]["count"]
    except:pass
    return last_count
count=latest_count()

Explorar Pase

In [9]:
conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password=os.getenv('CLAVE_POSGRES'),
        host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )
app=TradingHelper()
query = f"""
WITH pase AS (
    WITH CI AS (
        SELECT short_ticker, volumen_compra, precio_compra, timestamp, count AS count_CI
        FROM precios
        WHERE term = 'CI' 
          AND currency = 'ARS' 
          AND precio_compra IS NOT NULL 
          AND timestamp > '2024-08-20'
          AND to_char(timestamp, 'HH24:MI') > '11:05' AND to_char(timestamp, 'HH24:MI') < '16:30'
    ),
    hs AS (
        SELECT short_ticker, volumen_venta, precio_venta, timestamp, count AS count_24
        FROM precios
        WHERE term = '24hs' 
          AND currency = 'ARS' 
          AND precio_venta IS NOT NULL
          AND timestamp > '2024-08-20'
          AND to_char(timestamp, 'HH24:MI') > '11:05' AND to_char(timestamp, 'HH24:MI') < '16:30'
    )
    SELECT 
        CASE 
            WHEN (CI.precio_compra != 0 AND hs.precio_venta != 0) 
            THEN CI.precio_compra / hs.precio_venta 
            ELSE 0
        END AS ratio,
        CI.*, hs.volumen_venta, hs.precio_venta
    FROM CI 
    INNER JOIN hs 
        ON CI.count_CI = hs.count_24 
        AND CI.short_ticker = hs.short_ticker 
        AND to_char(CI.timestamp::timestamp, 'YYYY-MM-DD HH24:MI') = to_char(hs.timestamp::timestamp, 'YYYY-MM-DD HH24:MI')
)
SELECT *
FROM pase 
WHERE ratio > 1.00
ORDER BY ratio DESC;
"""

# Ejecuta la consulta SQL
cursor = conn.cursor()
cursor.execute(query)
# Load the result directly into a pandas DataFrame
df = pd.read_sql_query(query, conn)
df.sample(5)

import plotly.express as px
fig = px.scatter(x=df["timestamp"], y=df["ratio"],color = df["short_ticker"])
fig.add_hline(y=1.01, line_dash="dash", line_color="black", annotation_text="1.01", annotation_position="top left")
fig.show()

/tmp/ipykernel_105407/1661876784.py:51: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



In [10]:
tickers=pd.read_csv("tabla_tickers.csv")
df = pd.merge(df, tickers, on='short_ticker', how='inner')
df['vencimiento'] = pd.to_datetime(df['vencimiento'])
df['timestamp'] = pd.to_datetime(df['timestamp'])

# Restar las columnas
df['meses a finish'] = (df['vencimiento'] - df['timestamp'])/12
df = df[df['ratio'] > 1.01]

df.sample(5)

/tmp/ipykernel_105407/2347516346.py:3: UserWarning:

Parsing dates in %d/%m/%Y format when dayfirst=False (the default) was specified. Pass `dayfirst=True` or specify a format to silence this warning.



ratio short_ticker  volumen_compra  precio_compra  \
1100  1.008535        S13D4        500000.0        113.550   
1984  1.001430        S13D4       1000000.0        112.750   
1405  1.003599        S13D4        137803.0        114.601   
2586  1.000140        S13D4      38929472.0        114.016   
3989  1.000196        S30J5       1289507.0        101.900   

                      timestamp  count_ci  volumen_venta  precio_venta   tipo  \
1100 2024-08-30 14:18:06.333737      2175     90599982.0       112.589  lecap   
1984 2024-08-30 14:42:38.765052      2279     34413876.0       112.589  lecap   
1405 2024-09-09 15:02:47.671279       560     29619885.0       114.190  lecap   
2586 2024-09-10 13:00:46.060757       330      3527929.0       114.000  lecap   
3989 2024-09-10 12:21:49.917575       221      5000000.0       101.880  lecap   

     vencimiento             meses a finish  
1100  2025-02-28 15 days 02:48:29.472188583  
1984  2025-02-28    15 days 02:46:26.769579  
1405  2025-02-28 14 days 06:44:46.027393416  
2586  2025-02-28 14 days 04:54:56.161603583  
3989  2025-06-18 23 days 08:58:10.840202083

In [15]:
fig = px.scatter(x=df["meses a finish"], y=df["ratio"],color = df["short_ticker"],symbol=df["tipo"])
fig.add_hline(y=1.01, line_dash="dash", line_color="black", annotation_text="1.01", annotation_position="top left")
fig.show()

In [3]:
conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password=os.getenv('CLAVE_POSGRES'),
        host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )
app=TradingHelper()
portfolio=app.portfolio(mail="cirigliano.santiago@gmail.com")
tickers_in_portfolio=[]
for i in portfolio["tickers"]:
    ticker=i["ticker"]
    tickers_in_portfolio.append(ticker)
tickers_in_portfolio=tuple(tickers_in_portfolio[2:])
tickers_in_portfolio
while True: 
    count=latest_count()
    query = f"""
WITH pase AS (
    WITH CI AS (
        SELECT short_ticker, volumen_compra, precio_compra, timestamp, count AS count_CI
        FROM precios
        WHERE term = 'CI' 
          AND currency = 'ARS' 
          AND precio_compra IS NOT NULL 
          AND timestamp > '2024-09-01'
    ),
    hs AS (
        SELECT short_ticker, volumen_venta, precio_venta, timestamp, count AS count_24
        FROM precios
        WHERE term = '24hs' 
          AND currency = 'ARS' 
          AND precio_venta IS NOT NULL
          AND timestamp > '2024-09-01'
    )
    SELECT 
        CASE 
            WHEN (CI.precio_compra != 0 AND hs.precio_venta != 0) 
            THEN CI.precio_compra / hs.precio_venta 
            ELSE 0
        END AS ratio,
        CI.*, hs.*
    FROM CI 
    INNER JOIN hs 
        ON CI.count_CI = hs.count_24 
        AND CI.short_ticker = hs.short_ticker 
        AND strftime('%Y-%m-%d %H:%M', CI.timestamp) = strftime('%Y-%m-%d %H:%M', hs.timestamp)
)
SELECT *
FROM pase 
WHERE ratio > 1
ORDER BY ratio DESC;
"""

    # Ejecuta la consulta SQL
    cursor = conn.cursor()
    cursor.execute(query)
    # Load the result directly into a pandas DataFrame
    df = pd.read_sql_query(query, conn)

# Close the connection
conn.close()

# Display the DataFrame
print(df)

    # Obtén los nombres de las columnas
    columns = [desc[0] for desc in cursor.description]
    result_dict = [dict(zip(columns, row)) for row in cursor.fetchall()]
    #print(result_dict)
    if len(result_dict)>0:
        # Convierte los resultados en una lista de diccionarios
        result_dict = result_dict[0]
        print(result_dict)
        #Consuta el portfolio y se fija si tengo el ticker que tiene pase. Si lo tengo, captura cuantos nominales tengo
        app=TradingHelper()
        portfolio=app.portfolio(mail="cirigliano.santiago@gmail.com")
        # Inicializamos la variable amount_in_portfolio como None
        amount_in_portfolio = None
        # Iteramos sobre cada ticker en la lista de tickers del portfolio
        for ticker in portfolio["tickers"]:
            # Comprobamos si el ticker actual coincide con el short_ticker en result_dict
            if ticker["ticker"] == result_dict["short_ticker"]:
                stocks_available=app.stocks_available(mail="cirigliano.santiago@gmail.com",ticker=ticker["ticker"],term="CI",currency="pesos")
                if stocks_available["CI"]>0:
                    print("tengo el ticker en cartera en CI")  # Imprimimos un mensaje indicando que el ticker está en el portfolio
                    amount_in_portfolio=stocks_available["CI"]  # Capturamos la cantidad del ticker en la variable amount_in_portfolio
                    print(f"la cantidad en portfolio es de {amount_in_portfolio}")  # Imprimimos la cantidad capturada
                    break  # Salimos del bucle ya que encontramos el ticker
                elif stocks_available["CI"]==0:
                    break
        # Si amount_in_portfolio sigue siendo None, significa que no encontramos el ticker
        if amount_in_portfolio is None: 
            print("No tenemos el ticker en portfolio")  # Imprimimos un mensaje indicando que el ticker no está en el portfolio
        #si hay cantidad del ticker en portfolio
        else: #amount_in_portfolio is not None:
            amount_demanded=result_dict["volumen_venta"]
            print(f"la cantidad demandada en CI es {amount_demanded}")
            amount_offered=result_dict["volumen_compra"]
            print(f"la cantidad ofrecida en 24hs es {amount_offered}")
            amount=min(amount_in_portfolio,amount_demanded,amount_offered)
            print(f"La minima cantidad es {amount}")
            sell_order=app.place_sell_order(mail="cirigliano.santiago@gmail.com",ticker=result_dict["short_ticker"],quantity=amount,price=result_dict["precio_compra"],term="CI",currency="pesos")
            print(f"Orden de venta {sell_order}")
            order_status=app.cancel_order_if_still_open(mail="cirigliano.santiago@gmail.com",order_number=sell_order['Orden'])
            print(order_status)
            if order_status["Success"]=="EXECUTED":
                buy_order=app.place_buy_order(mail="cirigliano.santiago@gmail.com",ticker=result_dict["short_ticker"],quantity=amount,price=result_dict["precio_venta"],term="24",currency="pesos")
                print(f"Orden de compra {buy_order}")
                if buy_order["Success"] == True:
                    print("Negocio ATR")
                else: print(f"falló orden de compra {buy_order}")
            elif order_status["Success"] == True: pass

KeyboardInterrupt: 

In [5]:
from trading_helper import TradingHelper
app=TradingHelper()
response = app.get_snapshot(mail="cirigliano.santiago@gmail.com", ticker="S13D4")
response

[{'short_ticker': 'S13D4',
  'long_ticker': 'S13D4-0001-C-CT-ARS',
  'instrument_code': 'S13D4',
  'instrument_name': 'LECAP $ 4,50% 13/12/24',
  'instrument_short_name': 'LECAP DICIEMBRE 2024',
  'instrument_type': 'LETRAS',
  'instrument_subtype': None,
  'logo_file_name': 'ARG.jpg',
  'id_venue': 'BYMA',
  'id_session': 'CT',
  'id_segment': 'C',
  'settlement_days': 0,
  'currency': 'ARS',
  'price_factor': 100,
  'contract_size': 1,
  'min_lot_size': 1,
  'id_security': 115696221,
  'tick_size': 0.001,
  'date': '2024-09-04',
  'open': 113.5,
  'high': 114.2,
  'low': 112.998,
  'close': 113.054,
  'prev_close': 112.901,
  'last': 113.054,
  'bid': 113,
  'ask': 114.249,
  'bids': [{'size': 80000, 'price': 113},
   {'size': 250000, 'price': 112.75},
   {'size': 2197933, 'price': 112.051}],
  'asks': [{'size': 3666652, 'price': 114.249}],
  'turnover': 252295152.11,
  'volume': 222736959,
  'variation': 0.00135517,
  'term': 'CI',
  'id_tick_size_rule': 'BYMA_FIXED_INCOME',
  'is_f

In [6]:
from trading_helper import TradingHelper
app=TradingHelper()
response=app.get_snapshot(mail="cirigliano.santiago@gmail.com",ticker="AL30")
response

ApiException: Bad HTTP API Response. Error code: 400. Server response {"error":"invalid_grant","error_description":"Invalid Refresh Token: Session Expired (Inactivity)"}

In [ ]:
conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password=os.getenv('CLAVE_POSGRES'),
        host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )

cursor = conn.cursor()
count=latest_count()
print(count)
query = f"""with CI as(
        select short_ticker, volumen_compra, precio_compra, timestamp, count as count_CI
        from precios
        where short_ticker in ('T4X4','T5X4','T2X5','TDG24','TC25P','TX25','TX26','TX28','TZX25','TZX26',
        'TZX27','TZX28','TZXD5','TZXD6','TZXD7','TZV25','TV25','S30G4','S13S4','S30S4','S14O4',
        'S29N4','S17E5','S13D4','S31E5','S28F5','S31M5') 
        and term = 'CI' 
        and currency = 'ARS' 
        and precio_compra is not null 
        and count = {count}
        ),
        hs as (
        select short_ticker, volumen_venta, precio_venta, count as count_24
        from precios
        where short_ticker in ('T4X4','T5X4','T2X5','TDG24','TC25P','TX25','TX26','TX28','TZX25','TZX26',
        'TZX27','TZX28','TZXD5','TZXD6','TZXD7','TZV25','TV25','S30G4','S13S4','S30S4','S14O4',
        'S29N4','S17E5','S13D4','S31E5','S28F5','S31M5') 
        and term = '24hs' 
        and currency = 'ARS' 
        and precio_venta is not null
        and count = {count}
        )
        select *
        from hs
        order by count_24 desc
        """
# Ejecuta la consulta SQL
cursor.execute(query)

# Obtén los nombres de las columnas
columns = [desc[0] for desc in cursor.description]
result_dict = [dict(zip(columns, row)) for row in cursor.fetchall()]
result_dict

2186


[{'short_ticker': 'TX26',
  'volumen_venta': Decimal('59339'),
  'precio_venta': Decimal('1861'),
  'count_24': 2186},
 {'short_ticker': 'T4X4',
  'volumen_venta': Decimal('500000'),
  'precio_venta': Decimal('557.8'),
  'count_24': 2186},
 {'short_ticker': 'T5X4',
  'volumen_venta': Decimal('469162'),
  'precio_venta': Decimal('452'),
  'count_24': 2186},
 {'short_ticker': 'T2X5',
  'volumen_venta': Decimal('778311'),
  'precio_venta': Decimal('549'),
  'count_24': 2186},
 {'short_ticker': 'TC25P',
  'volumen_venta': Decimal('9605'),
  'precio_venta': Decimal('5028'),
  'count_24': 2186},
 {'short_ticker': 'TX25',
  'volumen_venta': Decimal('2714'),
  'precio_venta': Decimal('923.5'),
  'count_24': 2186},
 {'short_ticker': 'T4X4',
  'volumen_venta': Decimal('973'),
  'precio_venta': Decimal('556.8'),
  'count_24': 2186},
 {'short_ticker': 'T5X4',
  'volumen_venta': Decimal('60008212'),
  'precio_venta': Decimal('451'),
  'count_24': 2186},
 {'short_ticker': 'T2X5',
  'volumen_venta': 

Chequeo para cambio de dolares

In [ ]:
# Crear la query optimizada para seleccionar solo las filas de hoy
query = f"""
with dolar_mas_caro as (
with
vendo_dolares as 
(with DOLARES AS (
    SELECT
        CASE 
            WHEN RIGHT(short_ticker, 1) = 'D' THEN LEFT(short_ticker, LENGTH(short_ticker) - 1)
            ELSE short_ticker
        END AS short_ticker,
        precio_venta as dolares_precio_venta, 
        volumen_venta as dolares_volumen_venta, 
        count
    FROM precios
    WHERE timestamp >= '{today_start}'
    and count= {count}
    AND currency = 'USD' 
    AND term = 'CI'
    AND short_ticker in ('AL30',''GD30','AL35','GD35","AE38','GD38','AL41','GD41')
),
PESOS AS (
    SELECT short_ticker,
    precio_compra as pesos_precio_compra, 
    volumen_compra as pesos_volumen_compra,count
    FROM precios
    WHERE timestamp >= '{today_start}'
    and count = {count}
    AND currency = 'ARS' 
    AND term = '24hs'
    AND short_ticker in ('AL30',''GD30','AL35','GD35","AE38','GD38','AL41','GD41')
)
select pesos.short_ticker as ticker_a_vender_en_pesos,
pesos.pesos_precio_compra as precio_al_que_vendo_especie_en_pesos,
pesos.pesos_volumen_compra as volumen_al_que_vendo_especie_en_pesos,
pesos.count as count,
dolares.short_ticker as ticker_a_comprar_en_dolares,
dolares.dolares_precio_venta as precio_al_que_compro_especie_en_dolares,
dolares.dolares_volumen_venta as volumen_al_que_compro_especie_en_dolares

from pesos inner join dolares on pesos.short_ticker=dolares.short_ticker and pesos.count=dolares.count)
select *,
case when 1=1 then vendo_dolares.precio_al_que_vendo_especie_en_pesos/vendo_dolares.precio_al_que_compro_especie_en_dolares end as precio_venta_dolar
from vendo_dolares
order by precio_venta_dolar desc
limit 1),
dolar_mas_barato as (
with
compro_dolares as 
(with DOLARES AS (
    SELECT
        CASE 
            WHEN RIGHT(short_ticker, 1) = 'D' THEN LEFT(short_ticker, LENGTH(short_ticker) - 1)
            ELSE short_ticker
        END AS short_ticker,
        precio_compra as dolares_precio_compra, 
        volumen_compra as dolares_volumen_compra, 
        count
    FROM precios
    WHERE timestamp >= '{today_start}'
    and count= {count}
    AND currency = 'USD' 
    AND term = '24hs'
    AND short_ticker in ('AL30',''GD30','AL35','GD35","AE38','GD38','AL41','GD41')
),
PESOS AS (
    SELECT short_ticker,
    precio_venta as pesos_precio_venta, 
    volumen_venta as pesos_volumen_venta,count
    FROM precios
    WHERE timestamp >= '{today_start}'
    and count = {count}
    AND currency = 'ARS' 
    AND term = 'CI'
    AND short_ticker in ('AL30',''GD30','AL35','GD35","AE38','GD38','AL41','GD41')
)
select pesos.short_ticker as ticker_a_comprar_en_pesos,
pesos.pesos_precio_venta as precio_al_que_compro_especie_en_pesos,
pesos.pesos_volumen_venta as volumen_al_que_compro_especie_en_pesos,
pesos.count as count,
dolares.short_ticker as ticker_a_vender_en_dolares,
dolares.dolares_precio_compra as precio_al_que_vendo_especie_en_dolares,
dolares.dolares_volumen_compra as volumen_al_que_vendo_especie_en_dolares
from pesos 
inner join dolares on pesos.short_ticker=dolares.short_ticker and pesos.count=dolares.count)
select *,
case when 1=1 then compro_dolares.precio_al_que_compro_especie_en_pesos/compro_dolares.precio_al_que_vendo_especie_en_dolares end as precio_compra_dolar
from compro_dolares
order by precio_compra_dolar asc
limit 1)
select *,
case when 1=1 then dolar_mas_caro.precio_venta_dolar/dolar_mas_barato.precio_compra_dolar end as ratio
from dolar_mas_caro inner join dolar_mas_barato on dolar_mas_barato.count=dolar_mas_caro.count;
"""
while True:
    time.sleep(1)
    count=latest_count()
    cursor = conn.cursor()
    # Ejecuta la consulta SQL
    cursor.execute(query)
    # Obtén los nombres de las columnas
    columns = [desc[0] for desc in cursor.description]
    # Convierte los resultados en una lista de diccionarios
    result_dict = [dict(zip(columns, row)) for row in cursor.fetchall()][0]
    if result_dict["ratio"]>1.005:print(result_dict)


SyntaxError: syntax error at or near "GD30"
LINE 19:     AND short_ticker in ('AL30',''GD30','AL35','GD35","AE38'...
                                           ^


In [ ]:
from tqdm import tqdm
results=[]
latest=latest_count()
for count in tqdm(range(0,latest):
        # Crear la query optimizada para seleccionar solo las filas de hoy
    query = f"""
    with dolar_mas_caro as (
    with
    vendo_dolares as 
    (with DOLARES AS (
        SELECT
            CASE 
                WHEN RIGHT(short_ticker, 1) = 'D' THEN LEFT(short_ticker, LENGTH(short_ticker) - 1)
                ELSE short_ticker
            END AS short_ticker,
            precio_venta as dolares_precio_venta, 
            volumen_venta as dolares_volumen_venta, 
            count
        FROM precios
        WHERE timestamp >= '{today_start}'
        and count= {count}
        AND currency = 'USD' 
        AND term = 'CI'
    ),
    PESOS AS (
        SELECT short_ticker,
        precio_compra as pesos_precio_compra, 
        volumen_compra as pesos_volumen_compra,count
        FROM precios
        WHERE timestamp >= '{today_start}'
        and count = {count}
        AND currency = 'ARS' 
        AND term = '24hs'
    )
    select pesos.short_ticker as ticker_a_vender_en_pesos,
    pesos.pesos_precio_compra as precio_al_que_vendo_especie_en_pesos,
    pesos.pesos_volumen_compra as volumen_al_que_vendo_especie_en_pesos,
    pesos.count as count,
    dolares.short_ticker as ticker_a_comprar_en_dolares,
    dolares.dolares_precio_venta as precio_al_que_compro_especie_en_dolares,
    dolares.dolares_volumen_venta as volumen_al_que_compro_especie_en_dolares

    from pesos inner join dolares on pesos.short_ticker=dolares.short_ticker and pesos.count=dolares.count)
    select *,
    case when 1=1 then vendo_dolares.precio_al_que_vendo_especie_en_pesos/vendo_dolares.precio_al_que_compro_especie_en_dolares end as precio_venta_dolar
    from vendo_dolares
    order by precio_venta_dolar desc
    limit 1),
    dolar_mas_barato as (
    with
    compro_dolares as 
    (with DOLARES AS (
        SELECT
            CASE 
                WHEN RIGHT(short_ticker, 1) = 'D' THEN LEFT(short_ticker, LENGTH(short_ticker) - 1)
                ELSE short_ticker
            END AS short_ticker,
            precio_compra as dolares_precio_compra, 
            volumen_compra as dolares_volumen_compra, 
            count
        FROM precios
        WHERE timestamp >= '{today_start}'
        and count= {count}
        AND currency = 'USD' 
        AND term = '24hs'
    ),
    PESOS AS (
        SELECT short_ticker,
        precio_venta as pesos_precio_venta, 
        volumen_venta as pesos_volumen_venta,count
        FROM precios
        WHERE timestamp >= '{today_start}'
        and count = {count}
        AND currency = 'ARS' 
        AND term = 'CI'
    )
    select pesos.short_ticker as ticker_a_comprar_en_pesos,
    pesos.pesos_precio_venta as precio_al_que_compro_especie_en_pesos,
    pesos.pesos_volumen_venta as volumen_al_que_compro_especie_en_pesos,
    pesos.count as count,
    dolares.short_ticker as ticker_a_vender_en_dolares,
    dolares.dolares_precio_compra as precio_al_que_vendo_especie_en_dolares,
    dolares.dolares_volumen_compra as volumen_al_que_vendo_especie_en_dolares
    from pesos 
    inner join dolares on pesos.short_ticker=dolares.short_ticker and pesos.count=dolares.count)
    select *,
    case when 1=1 then compro_dolares.precio_al_que_compro_especie_en_pesos/compro_dolares.precio_al_que_vendo_especie_en_dolares end as precio_compra_dolar
    from compro_dolares
    order by precio_compra_dolar asc
    limit 1)
    select *,
    case when 1=1 then dolar_mas_caro.precio_venta_dolar/dolar_mas_barato.precio_compra_dolar end as ratio
    from dolar_mas_caro inner join dolar_mas_barato on dolar_mas_barato.count=dolar_mas_caro.count;
    """
    cursor = conn.cursor()

    # Ejecuta la consulta SQL
    cursor.execute(query)

    # Obtén los nombres de las columnas
    columns = [desc[0] for desc in cursor.description]

    # Convierte los resultados en una lista de diccionarios
    result_dict = [dict(zip(columns, row)) for row in cursor.fetchall()][0]
    results.append(result_dict)
    #if result_dict["ratio"]>1.001:print(result_dict)
results

100%|██████████| 5186/5186 [16:03<00:00,  5.38it/s]


[{'ticker_a_vender_en_pesos': 'AL30',
  'precio_al_que_vendo_especie_en_pesos': Decimal('66100'),
  'volumen_al_que_vendo_especie_en_pesos': Decimal('8769'),
  'count': 0,
  'ticker_a_comprar_en_dolares': 'AL30',
  'precio_al_que_compro_especie_en_dolares': Decimal('51.18'),
  'volumen_al_que_compro_especie_en_dolares': Decimal('52002'),
  'precio_venta_dolar': Decimal('1291.5201250488472059'),
  'ticker_a_comprar_en_pesos': 'GD35',
  'precio_al_que_compro_especie_en_pesos': Decimal('57040'),
  'volumen_al_que_compro_especie_en_pesos': Decimal('7828'),
  'ticker_a_vender_en_dolares': 'GD35',
  'precio_al_que_vendo_especie_en_dolares': Decimal('44.316'),
  'volumen_al_que_vendo_especie_en_dolares': Decimal('4748'),
  'precio_compra_dolar': Decimal('1287.1197761530824082'),
  'ratio': Decimal('1.0034187563405455')},
 {'ticker_a_vender_en_pesos': 'AL30',
  'precio_al_que_vendo_especie_en_pesos': Decimal('66120'),
  'volumen_al_que_vendo_especie_en_pesos': Decimal('2871'),
  'count': 1,
  

In [ ]:
ratios=[]
for result in results:
    ratios.append(result["ratio"])
# Crea el histograma
fig = px.histogram(ratios, 
                   nbins=20,  # Puedes ajustar el número de bins según sea necesario
                   title='Distribución de Probabilidad de Ratios',
                   labels={'value': 'Ratios'},
                   marginal='box',  # Agrega un boxplot en la parte superior
                   opacity=0.75)

# Muestra el histograma
fig.show()
# Ordena la lista de mayor a menor
ratios5 = sorted(ratios, reverse=True)[:5]
print("Top 5 valores más altos:", ratios5)

Top 5 valores más altos: [Decimal('1.0399500720746662'), Decimal('1.0399500720746662'), Decimal('1.0330294896385093'), Decimal('1.0330294896385093'), Decimal('1.0330294896385093')]


In [ ]:
x_values = list(range(len(ratios)))

# Crear el gráfico de dispersión
fig = px.scatter(x=x_values, y=ratios, 
                 labels={'x': 'Posición en la lista', 'y': 'Valores de Ratios'},
                 title='Gráfico de Dispersión de Ratios')

# Mostrar el gráfico
fig.show()

In [ ]:
import psycopg2
from datetime import datetime
import pandas as pd
conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password="Urbani7000",
        host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )

# Obtener la fecha de hoy
today_start = datetime.now().strftime('%Y-%m-%d 00:00:00')
today_end = datetime.now().strftime('%Y/%m/%d 23:59:59.999999')
while True:
    count=latest_count()

    # Crear la query optimizada para seleccionar solo las filas de hoy
    query = f"""
    WITH DOLARES AS (
        SELECT
            CASE 
                WHEN RIGHT(short_ticker, 1) = 'D' THEN LEFT(short_ticker, LENGTH(short_ticker) - 1)
                ELSE short_ticker
            END AS short_ticker,
            precio_venta, precio_compra,volumen_compra,volumen_venta, timestamp, count, currency
        FROM precios
        WHERE timestamp >= '{today_start}'
        AND count = {count} 
        AND currency = 'USD' 
        AND term = 'CI'
    ),
    PESOS AS (
        SELECT *
        FROM precios
        WHERE timestamp >= '{today_start}'
        AND count = {count} 
        AND currency = 'ARS' 
        AND term = 'CI'
    ) 
    SELECT     
        CASE 
            WHEN dolares.precio_compra IS NOT NULL AND pesos.precio_venta IS NOT NULL THEN 
                pesos.precio_venta / dolares.precio_compra 
            ELSE 
                NULL 
        END AS dolar_compra,
        
        CASE 
            WHEN dolares.precio_venta IS NOT NULL AND pesos.precio_compra IS NOT NULL THEN 
                pesos.precio_compra / dolares.precio_venta 
            ELSE 
                NULL 
        END AS dolar_venta,
        CASE 
            WHEN (pesos.precio_venta / dolares.precio_compra) IS NOT NULL 
            AND (pesos.precio_compra / dolares.precio_venta) IS NOT NULL THEN 
                (pesos.precio_compra / dolares.precio_venta) / (pesos.precio_venta / dolares.precio_compra) 
            ELSE 
                NULL 
        END AS ratio,
        pesos.short_ticker as pesos_short_ticker,
        pesos.currency as pesos_currency,
        pesos.volumen_venta as pesos_volumen_venta,
        pesos.precio_venta as pesos_precio_venta,
        pesos.volumen_compra as pesos_volumen_compra,
        pesos.precio_compra as pesos_precio_compra,
        CASE 
            WHEN dolares.short_ticker IS NOT NULL THEN 
                dolares.short_ticker || 'D'
            ELSE dolares.short_ticker 
        END AS dolares_short_ticker,
        dolares.volumen_venta as dolares_volumen_venta,
        dolares.precio_venta as dolares_precio_venta,
        dolares.volumen_compra as dolares_volumen_compra,
        dolares.precio_compra as dolares_precio_compra
    FROM pesos
    INNER JOIN DOLARES 
        ON PESOS.count = DOLARES.count 
        AND PESOS.short_ticker = DOLARES.short_ticker
    ORDER BY ratio DESC
    LIMIT 1;
    """
    cursor = conn.cursor()

    # Ejecuta la consulta SQL
    cursor.execute(query)

    # Obtén los nombres de las columnas
    columns = [desc[0] for desc in cursor.description]

    # Convierte los resultados en una lista de diccionarios
    result_dict = [dict(zip(columns, row)) for row in cursor.fetchall()][0]

    if result_dict["ratio"]>1.001:print(result_dict)
    #else: print(result_dict["ratio"])
    #else: print(result_dict["ratio"])

# Cerrar la conexión
#conn.close()

KeyboardInterrupt: 

In [ ]:
import psycopg2
from datetime import datetime
import pandas as pd
conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password="Urbani7000",
        host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )

# Obtener la fecha de hoy
today_start = datetime.now().strftime('%Y/%m/%d 00:00:00.000000')
today_end = datetime.now().strftime('%Y/%m/%d 23:59:59.999999')
count=latest_count()
print(count)
# Crear la query optimizada para seleccionar solo las filas de hoy
query = f"""
SELECT *
FROM precios
WHERE timestamp >= '2024/08/27 9:00:00' AND count = {count}"""# AND timestamp <= '{today_end}'
#"""

# Ejecutar la query y cargar los resultados en un DataFrame de pandas
df = pd.read_sql_query(query, conn)

# Cerrar la conexión
conn.close()

# Convertir la columna 'timestamp' a datetime con el formato especificado
df['timestamp'] = pd.to_datetime(df['timestamp'], format="%y/%m/%d %H:%M:%S.%f")
df['timestamp_s'] = pd.to_datetime(df['timestamp']).dt.strftime("%d/%m/%y %H:%M:%S")

df['short_ticker'] = df.apply(
    lambda row: row['short_ticker'][:-1] if row['currency'] == 'USD' and row['short_ticker'].endswith('D') else row['short_ticker'], 
    axis=1)
df= df[df['term'].isin(["CI"])]
ars = df[df['currency'].isin(["ARS"])]
usd = df[df['currency'].isin(["USD"])]
df = pd.merge(ars, usd, on=['short_ticker', 'term', 'count'], how='left',suffixes=("_ars","_usd"))
df["dolar_compra"]=df["precio_venta_ars"]/df["precio_compra_usd"]#tengo pesos y compro dolares
df["dolar_venta"]=df["precio_compra_ars"]/df["precio_venta_usd"]#tengo dolares y compro pesos

venta_dolares = df[["timestamp_s_ars","count","dolar_venta","dolar_compra","short_ticker"]].loc[df[["timestamp_s_ars","count","dolar_venta","dolar_compra","short_ticker"]].groupby('count')['dolar_venta'].idxmax()].sort_values(by='timestamp_s_ars', ascending=True)
compra_dolares = df[["timestamp_s_ars","count","dolar_venta","dolar_compra","short_ticker"]].loc[df[["timestamp_s_ars","count","dolar_venta","dolar_compra","short_ticker"]].groupby('count')['dolar_compra'].idxmin()].sort_values(by='timestamp_s_ars', ascending=True)
venta_dolares['timestamp_s_ars'] = pd.to_datetime(venta_dolares['timestamp_s_ars'], format='%d/%m/%y %H:%M:%S')
compra_dolares['timestamp_s_ars'] = pd.to_datetime(compra_dolares['timestamp_s_ars'], format='%d/%m/%y %H:%M:%S')
df = pd.merge(venta_dolares[["timestamp_s_ars","dolar_venta","count","short_ticker"]], compra_dolares[["dolar_compra","count","short_ticker"]], on=['count'], how='inner')
df["ratio"]=(df["dolar_venta"]-df["dolar_compra"])*100/df["dolar_compra"]

df.tail(5)
#deberia operar cuando el ratio es mayor a 0.05

1955


/tmp/ipykernel_118407/4276894997.py:24: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



timestamp_s_ars  dolar_venta  count short_ticker_x  dolar_compra  \
1951 2024-08-27 14:46:38  1286.796742   1951           GD30   1284.736482   
1952 2024-08-27 14:46:45  1286.796742   1952           GD30   1283.595711   
1953 2024-08-27 14:46:52  1286.838481   1953           AL30   1283.595711   
1954 2024-08-27 14:46:59  1287.035215   1954           AL30   1283.595711   
1955 2024-08-27 14:47:07  1299.935269   1955           AL35   1269.178082   

     short_ticker_y     ratio  
1951           AL35  0.160364  
1952           AL35  0.249380  
1953           AL35  0.252632  
1954           AL35  0.267959  
1955           AL35  2.423394

In [ ]:
import psycopg2
from datetime import datetime
import pandas as pd
conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password="Urbani7000",
        host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )

# Conectar a la base de datos
conn = sqlite3.connect('prices.db')

# Obtener la fecha de hoy
today_start = datetime.now().strftime('%Y/%m/%d 00:00:00.000000')
count = latest_count()
print(count)

# Crear la consulta SQL que incluye toda la lógica
query = f"""
WITH filtered_data AS (
    SELECT 
        p1.timestamp AS timestamp_ars,
        p1.short_ticker AS short_ticker_ars,
        p1.currency AS currency_ars,
        p1.term AS term_ars,
        p1.count AS count_ars,
        p1.precio_venta AS precio_venta_ars,
        p1.precio_compra AS precio_compra_ars,
        p2.timestamp AS timestamp_usd,
        p2.short_ticker AS short_ticker_usd,
        p2.currency AS currency_usd,
        p2.term AS term_usd,
        p2.count AS count_usd,
        p2.precio_venta AS precio_venta_usd,
        p2.precio_compra AS precio_compra_usd,
        p1.short_ticker
    FROM precios p1
    LEFT JOIN precios p2 ON p1.short_ticker = p2.short_ticker 
    AND p1.term = p2.term 
    AND p1.count = p2.count 
    AND p2.currency = 'USD'
    WHERE p1.currency = 'ARS'
    AND p1.timestamp >= '2024/08/27 9:00:00' 
    AND p1.count >= {count}
    AND p1.term = 'CI'
),
calc_dolar AS (
    SELECT 
        timestamp_ars,
        count_ars AS count,
        short_ticker,
        (precio_compra_ars / precio_venta_usd) AS dolar_venta,
        (precio_venta_ars / precio_compra_usd) AS dolar_compra
    FROM filtered_data
)
SELECT 
    v.timestamp_ars AS timestamp_s_ars,
    v.count,
    v.dolar_venta,
    c.dolar_compra,
    v.short_ticker
FROM calc_dolar v
JOIN calc_dolar c ON v.count = c.count
WHERE v.dolar_venta = (
    SELECT MAX(dolar_venta)
    FROM calc_dolar
    WHERE count = v.count
)
AND c.dolar_compra = (
    SELECT MIN(dolar_compra)
    FROM calc_dolar
    WHERE count = c.count
)
ORDER BY v.timestamp_ars ASC;
"""

# Ejecutar la query y cargar los resultados en un DataFrame de pandas
df = pd.read_sql_query(query, conn)

# Cerrar la conexión
conn.close()

# Convertir la columna 'timestamp_s_ars' a datetime con el formato especificado
df['timestamp_s_ars'] = pd.to_datetime(df['timestamp_s_ars'], format='%d/%m/%y %H:%M:%S')

# Calcular el ratio
df["ratio"] = df["dolar_venta"] / df["dolar_compra"]

#df["ratio"] = (df["dolar_venta"] - df["dolar_compra"]) * 100 / df["dolar_compra"]


2792


DatabaseError: Execution failed on sql '
WITH filtered_data AS (
    SELECT 
        p1.timestamp AS timestamp_ars,
        p1.short_ticker AS short_ticker_ars,
        p1.currency AS currency_ars,
        p1.term AS term_ars,
        p1.count AS count_ars,
        p1.precio_venta AS precio_venta_ars,
        p1.precio_compra AS precio_compra_ars,
        p2.timestamp AS timestamp_usd,
        p2.short_ticker AS short_ticker_usd,
        p2.currency AS currency_usd,
        p2.term AS term_usd,
        p2.count AS count_usd,
        p2.precio_venta AS precio_venta_usd,
        p2.precio_compra AS precio_compra_usd,
        p1.short_ticker
    FROM precios p1
    LEFT JOIN precios p2 ON p1.short_ticker = p2.short_ticker 
    AND p1.term = p2.term 
    AND p1.count = p2.count 
    AND p2.currency = 'USD'
    WHERE p1.currency = 'ARS'
    AND p1.timestamp >= '2024/08/27 9:00:00' 
    AND p1.count >= 2792
    AND p1.term = 'CI'
),
calc_dolar AS (
    SELECT 
        timestamp_ars,
        

In [ ]:
import plotly.graph_objs as go
import pandas as pd

# Crear los traces para 'dolar_compra' y 'dolar_venta'
trace = go.Scatter(
    x=df["timestamp_s_ars"],
    y=df["ratio"],
    mode='markers',
    name='Ratio',
    marker=dict(color='blue'),
    hovertext=df.apply(lambda row: f"Count: {row['count']}<br>ratio: {row['ratio']}<br>Dólar Venta: {row['dolar_venta']}<br>Dólar Compra: {row['dolar_compra']}<br>Short Ticker X: {row['short_ticker_x']}<br>Short Ticker Y: {row['short_ticker_y']}", axis=1),
    hoverinfo='text'
)

# Crear la figura y agregar los traces
fig = go.Figure(data=[trace])

# Configurar el layout
fig.update_layout(
    title="Ratio",
    xaxis_title="Timestamp",
    yaxis_title="Ratio"
)

# Mostrar el gráfico
fig.show()


In [ ]:
import plotly.graph_objs as go
import pandas as pd

# Supongamos que ya tienes un DataFrame llamado df con las columnas mencionadas

# Crear los traces para 'dolar_compra' y 'dolar_venta'
trace_compra = go.Scatter(
    x=compra_dolares["timestamp_s_ars"],
    y=compra_dolares["dolar_compra"],
    mode='markers',
    name='Dólar Compra',
    marker=dict(color='blue')
)

trace_venta = go.Scatter(
    x=venta_dolares["timestamp_s_ars"],
    y=venta_dolares["dolar_venta"],
    mode='markers',
    name='Dólar Venta',
    marker=dict(color='red')
)

# Crear la figura y agregar los traces
fig = go.Figure(data=[trace_compra, trace_venta])

# Configurar el layout
fig.update_layout(
    title="Dólar Compra y Venta vs. Timestamp",
    xaxis_title="Timestamp",
    yaxis_title="Valor del Dólar",
    legend_title="Tipo de Dólar"
)

# Mostrar el gráfico
fig.show()

In [ ]:
ratio={"numerador":{"short_ticker":"AL30", "currency":"ARS","term":"CI"},
       "denominador":{"short_ticker":"GD30", "currency":"ARS","term":"CI"}}

# Filtrar los datos para el numerador
numerador_df = df[
    (df['short_ticker'] == ratio['numerador']['short_ticker']) &
    (df['currency'] == ratio['numerador']['currency']) &
    (df['term'] == ratio['numerador']['term'])
]
print(numerador_df.shape)

# Filtrar los datos para el denominador
denominador_df = df[
    (df['short_ticker'] == ratio['denominador']['short_ticker']) &
    (df['currency'] == ratio['denominador']['currency']) &
    (df['term'] == ratio['denominador']['term'])
]
print(denominador_df.shape)

# Merge de los DataFrames por la columna timestamp
merged_df = pd.merge(numerador_df, denominador_df, on='timestamp_s', suffixes=('_numerador', '_denominador'))
#merged_df['timestamp_s'] = pd.to_datetime(df['timestamp_s'], format='%d/%m/%y %H:%M:%S').dt.time

# Calcular el ratio (por ejemplo, usando precio de compra)
merged_df['ratio'] = merged_df['precio_venta_numerador'] / merged_df['precio_compra_denominador']

# Calcular la media móvil de 30 períodos
merged_df['moving_average_30'] = merged_df['ratio'].rolling(window=30).mean()

# Calcular la desviación estándar para la media móvil de 30 períodos
merged_df['std_dev_30'] = merged_df['ratio'].rolling(window=30).std()

# Calcular las Bandas de Bollinger
merged_df['bollinger_upper'] = merged_df['moving_average_30'] + (merged_df['std_dev_30'] * 2.5)
merged_df['bollinger_lower'] = merged_df['moving_average_30'] - (merged_df['std_dev_30'] * 2.5)
print(merged_df.shape)

# Graficar el ratio en función del tiempo
fig = go.Figure()

# Añadir la traza para el ratio
fig.add_trace(go.Scatter(
    x=merged_df['timestamp_s'],
    y=merged_df['ratio'],
    mode='lines',
    name=f"Ratio {ratio['numerador']['short_ticker']}/{ratio['denominador']['short_ticker']}",
))

# Añadir la traza para la media móvil de 30 períodos
fig.add_trace(go.Scatter(
    x=merged_df['timestamp_s'],
    y=merged_df['moving_average_30'],
    mode='lines',
    name='Media Móvil 30 Períodos',
    line=dict(dash='dash')  # Línea discontinua para diferenciar
))

# Añadir la traza para la Banda de Bollinger Superior
fig.add_trace(go.Scatter(
    x=merged_df['timestamp_s'],
    y=merged_df['bollinger_upper'],
    mode='lines',
    name='Banda de Bollinger Superior',
    line=dict(color='rgba(255, 0, 0, 0.5)')  # Color rojo con opacidad
))

# Añadir la traza para la Banda de Bollinger Inferior
fig.add_trace(go.Scatter(
    x=merged_df['timestamp_s'],
    y=merged_df['bollinger_lower'],
    mode='lines',
    name='Banda de Bollinger Inferior',
    line=dict(color='rgba(0, 0, 255, 0.5)')  # Color azul con opacidad
))

# Configurar el diseño del gráfico
fig.update_layout(
    title=f"Ratio {ratio['numerador']['short_ticker']}/{ratio['denominador']['short_ticker']} en función del tiempo",
    xaxis_title="Tiempo",
    yaxis_title="Ratio",
    template="plotly_dark"
)

fig.show()

(1201, 9)
(1201, 9)
(580, 22)


In [ ]:
# Inicializa las variables para almacenar las sumas
suma_precio_venta = []
suma_precio_compra = []

# Itera sobre cada fila y aplica las condiciones
for _, row in merged_df.iterrows():
    if row['ratio'] > row['bollinger_upper']:
        suma_precio_venta.append(row['precio_venta_numerador'])
    elif row['ratio'] < row['bollinger_lower']:
        suma_precio_compra.append(row['precio_compra_numerador'])
print(suma_precio_compra)
print(suma_precio_venta)

# Calcula el retorno como suma de ventas menos suma de compras (esto puede ajustarse según tu definición de retorno)
retorno = (sum(suma_precio_venta) - sum(suma_precio_compra))/suma_precio_venta[0]
retorno

[64250.0, 64450.0, 64390.0]
[64330.0, 64320.0, 64330.0, 64400.0, 64400.0, 64420.0, 64410.0, 65480.0, 65480.0, 65480.0]


7.0567386911238925

In [ ]:
merged_df

short_ticker_numerador currency_numerador term_numerador  \
0                     AL30                ARS           24hs   
1                     AL30                ARS           24hs   
2                     AL30                ARS           24hs   
3                     AL30                ARS           24hs   
4                     AL30                ARS           24hs   
..                     ...                ...            ...   
575                   AL30                ARS           24hs   
576                   AL30                ARS           24hs   
577                   AL30                ARS           24hs   
578                   AL30                ARS           24hs   
579                   AL30                ARS           24hs   

     volumen_venta_numerador  precio_venta_numerador  \
0                    12057.0                 64370.0   
1                     2057.0                 64370.0   
2                    21000.0                 64360.0   
3                      500.0                 64370.0   
4                    15750.0                 64370.0   
..                       ...                     ...   
575                  50000.0                 66360.0   
576                    315.0                 65520.0   
577                    315.0                 65520.0   
578                    315.0                 65520.0   
579                    315.0                 65520.0   

     volumen_compra_numerador  precio_compra_numerador  \
0                     49234.0                  64380.0   
1                     51700.0                  64380.0   
2                     63267.0                  64390.0   
3                     60093.0                  64390.0   
4                     44827.0                  64390.0   
..                        ...                      ...   
575                    1407.0                  64420.0   
576                    1757.0                  64420.0   
577                    1757.0                  64420.0   
578                    1757.0                  64420.0   
579                   23757.0                  64420.0   

           timestamp_numerador        timestamp_s short_ticker_denominador  \
0   2024-08-23 14:15:57.109844  23/08/24 14:15:57                     GD30   
1   2024-08-23 14:16:14.113081  23/08/24 14:16:14                     GD30   
2   2024-08-23 14:17:20.072922  23/08/24 14:17:20                     GD30   
3   2024-08-23 14:17:35.339943  23/08/24 14:17:35                     GD30   
4   2024-08-23 14:17:52.130611  23/08/24 14:17:52                     GD30   
..                         ...                ...                      ...   
575 2024-08-23 16:58:36.137079  23/08/24 16:58:36                     GD30   
576 2024-08-23 16:59:07.569180  23/08/24 16:59:07                     GD30   
577 2024-08-23 16:59:25.180249  23/08/24 16:59:25                     GD30   
578 2024-08-23 16:59:33.480868  23/08/24 16:59:33                     GD30   
579 2024-08-23 16:59:57.447485  23/08/24 16:59:57                     GD30   

     ... volumen_venta_denominador precio_venta_denominador  \
0    ...                      87.0                  67200.0   
1    ...                      87.0                  67200.0   
2    ...                      87.0                  67200.0   
3    ...                      87.0                  67200.0   
4    ...                      87.0                  67200.0   
..   ...                       ...                      ...   
575  ...                       1.0                  67380.0   
576  ...                       1.0                  67380.0   
577  ...                       1.0                  67380.0   
578  ...                       1.0                  67380.0   
579  ...                       1.0                  67380.0   

     volumen_compra_denominador  precio_compra_denominador  \
0                        8001.0                    67230.0   
1                        8001.0                

In [ ]:
def plot_bohlinger(ratio):
    import sqlite3
    import pandas as pd
    from datetime import datetime
    # Conectarse a la base de datos antes de realizar cualquier cálculo
    conn = sqlite3.connect('prices.db')

    # Obtener la fecha de hoy
    today_start = datetime.now().strftime('%y/%m/%d 00:00:00.000000')
    today_end = datetime.now().strftime('%y/%m/%d 23:59:59.999999')

    # Query SQL que realiza la mayoría de las transformaciones
    query = f"""
    WITH numerador AS (
        SELECT 
            timestamp, 
            SUBSTR(timestamp, 1, 17) AS timestamp_s,
            precio_venta AS precio_venta_numerador
        FROM precios
        WHERE 
            short_ticker = '{ratio['numerador']['short_ticker']}' AND
            currency = '{ratio['numerador']['currency']}' AND
            term = '{ratio['numerador']['term']}' AND
            timestamp >= '{today_start}' AND 
            timestamp <= '{today_end}'
    ),
    denominador AS (
        SELECT 
            timestamp, 
            SUBSTR(timestamp, 1, 17) AS timestamp_s,
            precio_compra AS precio_compra_denominador
        FROM precios
        WHERE 
            short_ticker = '{ratio['denominador']['short_ticker']}' AND
            currency = '{ratio['denominador']['currency']}' AND
            term = '{ratio['denominador']['term']}' AND
            timestamp >= '{today_start}' AND 
            timestamp <= '{today_end}'
    )
    SELECT 
        numerador.timestamp, 
        numerador.timestamp_s,
        numerador.precio_venta_numerador, 
        denominador.precio_compra_denominador,
        (numerador.precio_venta_numerador / denominador.precio_compra_denominador) AS ratio
    FROM numerador
    INNER JOIN denominador 
    ON numerador.timestamp_s = denominador.timestamp_s
    """

    # Ejecutar la query y cargar los resultados en un DataFrame de pandas
    merged_df = pd.read_sql_query(query, conn)

    # Cerrar la conexión
    conn.close()

    # Calcular la media móvil de 30 períodos
    merged_df['moving_average_30'] = merged_df['ratio'].rolling(window=30).mean()

    # Calcular la desviación estándar para la media móvil de 30 períodos
    merged_df['std_dev_30'] = merged_df['ratio'].rolling(window=30).std()

    # Calcular las Bandas de Bollinger
    merged_df['bollinger_upper'] = merged_df['moving_average_30'] + (merged_df['std_dev_30'] * 2.5)
    merged_df['bollinger_lower'] = merged_df['moving_average_30'] - (merged_df['std_dev_30'] * 2.5)
    return merged_df
df=plot_bohlinger(ratio={"numerador":{"short_ticker":"AL35", "currency":"ARS","term":"24hs"},
       "denominador":{"short_ticker":"AE38", "currency":"ARS","term":"24hs"}})

timestamp        timestamp_s  precio_venta_numerador  \
421  24/08/21 14:04:46.097087  24/08/21 14:04:46                 55260.0   

     precio_compra_denominador     ratio  moving_average_30  std_dev_30  \
421                    57870.0  0.954899           0.954879    0.000175   

     bollinger_upper  bollinger_lower  
421         0.955317         0.954441

In [ ]:
#COMPRA DOLARES A 48 HS

# Establecer conexión con la base de datos
import sqlite3
import pandas as pd
import plotly.express as px
from datetime import datetime as dt,timedelta
import psycopg2
def precios_de_hoy():
    data=[]
    # Conectar a la nueva base de datos Prices
    conn = psycopg2.connect(
        dbname="prices",
        user="postgres",
        password="Urbani7000",
        host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
    )
    # Get today's date in the required format
    yesterday = (dt.now()-timedelta(days=1)).strftime("%d/%m/%y")

    # Modify the query to filter rows for today's date
    query = f"SELECT * FROM precios WHERE (short_ticker = 'BPOC7' or short_ticker = 'BPOD7') and term='CI' and timestamp > '{yesterday}'"

    cursor = conn.cursor()
    cursor.execute(query)

    # Fetch all rows from the query result
    rows = cursor.fetchall()

    # Fetch column names
    columns = [description[0] for description in cursor.description]

    # Create dictionaries representing rows
    for row in rows:
        data.append(dict(zip(columns, row)))

    # Close the connection
    conn.close()
    # Convert data list to DataFrame
    df = pd.DataFrame(data)
    df['timestamp'] = pd.to_datetime(df['timestamp'], format="%d/%m/%y %H:%M:%S.%f")
    df['timestamp_s'] = pd.to_datetime(df['timestamp']).dt.strftime("%d/%m/%y %H:%M:%S")

    # Create a new column 'ticker_time' by concatenating 'short_ticker' and 'timestamp_s'
    df["ticker_time"]=df["short_ticker"]+" "+df["timestamp_s"]
    return df

df=precios_de_hoy()
df.sample(5)

short_ticker currency term  volumen_venta  precio_venta  volumen_compra  \
59        BPOD7      ARS   CI          705.0       89670.0            10.0   
28        BPOD7      ARS   CI          100.0       90010.0           100.0   
79        BPOD7      ARS   CI          100.0       89450.0            10.0   
53        BPOD7      ARS   CI          705.0       89670.0            10.0   
0         BPOC7      ARS   CI         4562.0       95790.0             9.0   

    precio_compra                  timestamp        timestamp_s  \
59        89930.0 2024-07-16 14:02:39.923913  16/07/24 14:02:39   
28        90060.0 2024-07-16 13:08:05.700576  16/07/24 13:08:05   
79        89550.0 2024-07-16 14:56:36.717117  16/07/24 14:56:36   
53        89930.0 2024-07-16 14:02:36.239731  16/07/24 14:02:36   
0         95930.0 2024-07-16 12:36:07.840998  16/07/24 12:36:07   

                ticker_time  
59  BPOD7 16/07/24 14:02:39  
28  BPOD7 16/07/24 13:08:05  
79  BPOD7 16/07/24 14:56:36  
53  BPOD7 16/07/24 14:02:36  
0   BPOC7 16/07/24 12:36:07

In [ ]:
import psycopg2
from psycopg2 import sql

# Conectar a la nueva base de datos Prices
conn = psycopg2.connect(
    dbname="prices",
    user="postgres",
    password="Urbani7000",
    host="127.0.0.1"#"/var/run/postgresql"  # Usar Unix domain socket en lugar de host y puerto
)

# Crear un cursor
cursor = conn.cursor()

cursor.execute("""
    ALTER TABLE precios
    ADD COLUMN short_ticker VARCHAR(20),
    ADD COLUMN currency VARCHAR(10),
    ADD COLUMN term VARCHAR(10),
    ADD COLUMN volumen_venta DECIMAL,
    ADD COLUMN precio_venta DECIMAL,
    ADD COLUMN volumen_compra DECIMAL,
    ADD COLUMN precio_compra DECIMAL,
    ADD COLUMN timestamp TIMESTAMP
""")

# Confirmar los cambios
conn.commit()

# Cerrar la conexión
cursor.close()
conn.close()


In [ ]:
import sqlite3

# Conectar a la base de datos SQLite
conn = sqlite3.connect("prices.db")

# Crear un cursor
cursor = conn.cursor()

# Ejecutar una consulta para obtener los nombres de las columnas de la tabla
cursor.execute("PRAGMA table_info(precios)")

# Obtener los resultados
columns = cursor.fetchall()

# Mostrar los nombres de las columnas
column_names = [column[1] for column in columns]
print("Nombres de las columnas:", column_names)

# Cerrar la conexión
cursor.close()
conn.close()


Nombres de las columnas: ['short_ticker', 'currency', 'term', 'volumen_venta', 'precio_venta', 'volumen_compra', 'precio_compra', 'timestamp']


In [ ]:
from trading_helper import TradingHelper
app=TradingHelper()
portfolio=app.portfolio(mail="cirigliano.santiago@gmail.com")
for ticker in portfolio["tickers"]:
    if ticker["ticker"]=="TZX25":
        amount=ticker["amount"]

{'total': {'ars': 967197.4357143192, 'usd': 748.1085138105273},
 'tickers': [{'id_instrument': None,
   'id_security': None,
   'short_ticker': None,
   'ticker': 'AR$',
   'type': None,
   'subtype': None,
   'instrument_name': None,
   'instrument_short_name': None,
   'instrument_code': None,
   'quantity': 7328.95,
   'amount': 7328.95,
   'amount_usd': 5.668801104959848,
   'last': 1,
   'variation': None,
   'logo_file_name': 'ars.jpg'},
  {'id_instrument': None,
   'id_security': None,
   'short_ticker': None,
   'ticker': 'US$ MEP',
   'type': None,
   'subtype': None,
   'instrument_name': None,
   'instrument_short_name': None,
   'instrument_code': None,
   'quantity': 11.72,
   'amount': 15152.2857143192,
   'amount_usd': 11.72,
   'last': 1292.85714286,
   'variation': None,
   'logo_file_name': 'usd.jpg'},
  {'id_instrument': 864657,
   'id_security': 107219590,
   'short_ticker': 'BPOD7',
   'ticker': 'BPOD7',
   'type': 'BONOS_PUBLICOS',
   'subtype': None,
   'instrume

In [ ]:
from trading_helper import TradingHelper
app=TradingHelper()
order=app.place_buy_order(mail="cirigliano.santiago@gmail.com",ticker="AL30",quantity=5,price=64710,term="CI",currency="pesos")

AL30-0001-C-CT-ARS


order {'Success': True, 'Orden': '9b342ae1-5fa8-4bff-bf7f-a4dbf72edda7'}
{'Success': True, 'Orden': '9b342ae1-5fa8-4bff-bf7f-a4dbf72edda7'}


{'Success': True, 'Orden': '9b342ae1-5fa8-4bff-bf7f-a4dbf72edda7'}

In [ ]:
#VENTA DOLARES A 48 HS

# Establecer conexión con la base de datos
import sqlite3
import pandas as pd
import plotly.express as px
def precio_vender_dolares_al30():
    data=[]
    conn = sqlite3.connect("prices.db")

    query = f"SELECT * FROM precios WHERE (currency = 'USD' and term ='CI' and precio_compra > 0 and short_ticker='AL30D') or (currency = 'ARS' and term ='48hs' and precio_venta > 0 and short_ticker='AL30') order by timestamp desc LIMIT 4"

    cursor = conn.cursor()
    cursor.execute(query)

    # Fetch all rows from the query result
    rows = cursor.fetchall()

    # Fetch column names
    columns = [description[0] for description in cursor.description]

    # Create dictionaries representing rows
    for row in rows:
        data.append(dict(zip(columns, row)))

    # Close the connection
    conn.close()

    # Convert data list to DataFrame
    df = pd.DataFrame(data)
    df['timestamp'] = pd.to_datetime(df['timestamp'], format="%d/%m/%y %H:%M:%S.%f")

    df['timestamp_s'] = pd.to_datetime(df['timestamp']).dt.strftime("%d/%m/%y %H:%M:%S")

    # Create a new column 'ticker_time' by concatenating 'short_ticker' and 'timestamp_s'
    df["ticker_time"]=df["short_ticker"]+" "+df["timestamp_s"]

    # Filter for immediate purchase in ARS
    compra = df[df['term'].isin(["CI"])][df['currency'].isin(["USD"])]
    compra["precio_compra"]=compra["precio_compra"]*1.006

    # Filter for sale in USD after 48 hours
    venta = df[df['term'].isin(["48hs"])][df['currency'].isin(["ARS"])]
    venta["precio_venta"]=venta["precio_venta"]*0.994

    # Apply function to clean 'D' from ticker symbols in the 'venta' DataFrame
    compra['ticker_time'] = compra['ticker_time'].apply(remove_d_from_ticker)

    # Merge 'compra' and 'venta' DataFrames on 'ticker_time', keeping relevant columns
    df=pd.merge(compra[['short_ticker','currency','term', 'precio_compra','timestamp','ticker_time']],
                venta[['precio_venta',"ticker_time"]],
                how="inner",
                on="ticker_time")

    # Calculate dollar price as the ratio of 'precio_compra' to 'precio_venta'
    df["precio_dolar"]=df["precio_venta"]/df["precio_compra"]
    max_row = df.loc[df['timestamp'].idxmax()]
    timestamp = max_row['timestamp']
    current_time = dt.now()
    if current_time - timestamp > timedelta(minutes=5):
        return "Too old"
    else: return max_row["precio_dolar"]
precio_dolar_venta=precio_vender_dolares_al30()
print(precio_dolar_venta)

992.1818339375934


/tmp/ipykernel_11714/2807683390.py:39: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/tmp/ipykernel_11714/2807683390.py:43: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

